In [2]:
# NOTE: using pandas proved not practical
from pathlib import Path
from time import perf_counter
from collections import Counter
from itertools import chain
import json
from pprint import pprint

In [2]:
profession = Counter();
t1 = perf_counter()
with open(Path('data') / 'name.basics.tsv', encoding='utf-8') as f:
    column = {}
    for i, p in enumerate(f.readline().strip().split('\t')):
        column[p.strip()] = i
    for line in f:
        parts = line.strip().split('\t')
        glist = parts[column['primaryProfession']].strip().split(',')
        if len(glist) and glist[0] != '\\N':
            profession.update(glist)
del profession['']  # ?trailing comma?
print(perf_counter() - t1, 's')

18.6012343679904 s


In [3]:
pprint(profession)

Counter({'actor': 3080545,
         'actress': 1864307,
         'miscellaneous': 1386144,
         'producer': 1177175,
         'writer': 876570,
         'camera_department': 788093,
         'director': 716912,
         'art_department': 471987,
         'sound_department': 386120,
         'cinematographer': 382510,
         'editor': 354594,
         'composer': 330296,
         'music_department': 267988,
         'assistant_director': 258027,
         'visual_effects': 238331,
         'make_up_department': 225327,
         'animation_department': 216384,
         'production_manager': 208340,
         'editorial_department': 188765,
         'soundtrack': 171205,
         'costume_department': 156641,
         'transportation_department': 101682,
         'art_director': 92793,
         'stunts': 88323,
         'script_department': 86774,
         'location_management': 83672,
         'production_designer': 80765,
         'costume_designer': 75823,
         'special_effects

In [4]:
title_types = Counter();  genres = Counter();  #  title.basics
t1 = perf_counter()
with open(Path('data') / 'title.basics.tsv', encoding='utf-8') as f:
    column = {}
    for i, p in enumerate(f.readline().strip().split('\t')):
        column[p.strip()] = i
    for line in f:
        parts = line.strip().split('\t')
        title_type = parts[column['titleType']]
        if title_type != '\\N':
            title_types[title_type] += 1
        glist = parts[column['genres']].strip().split(',')
        if len(glist) and glist[0] != '\\N':
            genres.update(glist)
print(perf_counter() - t1, 's')


21.897611982014496 s


In [5]:
pprint(title_types)
pprint(genres)

Counter({'tvEpisode': 8115351,
         'short': 982948,
         'movie': 674011,
         'video': 289054,
         'tvSeries': 258546,
         'tvMovie': 144651,
         'tvMiniSeries': 52999,
         'tvSpecial': 46249,
         'videoGame': 37687,
         'tvShort': 10275,
         'tvPilot': 1})
Counter({'Drama': 3017091,
         'Comedy': 2099840,
         'Talk-Show': 1303202,
         'Short': 1157127,
         'Documentary': 1011720,
         'Romance': 988474,
         'News': 947675,
         'Family': 785825,
         'Reality-TV': 598622,
         'Animation': 534719,
         'Crime': 443291,
         'Action': 436663,
         'Adventure': 416227,
         'Music': 400045,
         'Game-Show': 387113,
         'Adult': 333307,
         'Sport': 253523,
         'Fantasy': 215414,
         'Mystery': 215052,
         'Horror': 190430,
         'Thriller': 175689,
         'History': 156752,
         'Biography': 114750,
         'Sci-Fi': 114416,
         'Musical'

In [6]:
taka_types = Counter(); taka_region = Counter(); taka_lang = Counter(); # title.akas
taka_attributes = Counter() # not enum, but we are curious about the possible values
t1 = perf_counter()
with open(Path('data') / 'title.akas.tsv', encoding='utf-8') as f:
    column = {}
    for i, p in enumerate(f.readline().strip().split('\t')):
        column[p.strip()] = i
    for line in f:
        parts = line.strip().split('\t')
        region = parts[column['region']]
        if region != '\\N':
            taka_region[region] += 1
        lang = parts[column['language']]
        if lang != '\\N':
            taka_lang[lang] += 1
        # there is a quirk in data, some include \u0002 instead of comma
        phase1 = parts[column['types']].strip().split(',')
        phase2 = [p.split('\x02') for p in phase1]
        glist = list(chain.from_iterable(phase2))
        if len(glist) and glist[0] != '\\N':
            taka_types.update(glist)
        glist = parts[column['attributes']].strip().split(',')
        if len(glist) and glist[0] != '\\N':
            taka_attributes.update(glist)            
print(perf_counter() - t1, 's')

103.84395928200684 s


In [7]:
pprint(taka_types)
pprint(taka_region)
pprint(taka_lang)
pprint(taka_attributes)

Counter({'imdbDisplay': 3759642,
         'original': 1849964,
         'alternative': 123541,
         'working': 56975,
         'dvd': 22456,
         'video': 21711,
         'festival': 20579,
         'tv': 19114})
Counter({'DE': 4684314,
         'JP': 4682243,
         'FR': 4674751,
         'IN': 4619888,
         'ES': 4591991,
         'IT': 4571384,
         'PT': 4491127,
         'US': 1511997,
         'GB': 476165,
         'CA': 261353,
         'XWW': 184904,
         'AU': 161742,
         'BR': 125841,
         'MX': 105547,
         'RU': 105119,
         'GR': 95004,
         'PL': 93841,
         'FI': 89115,
         'SE': 80852,
         'HU': 78171,
         'NL': 65062,
         'PH': 62498,
         'AR': 62390,
         'NO': 60236,
         'DK': 57630,
         'TR': 55223,
         'XWG': 52547,
         'CN': 43547,
         'SUHH': 39593,
         'TW': 37274,
         'EC': 36940,
         'BE': 36572,
         'HK': 36395,
         'KR': 34367,
    

In [3]:
tp_categories = Counter(); # title.principals
chars = Counter()
t1 = perf_counter()
job_max_len = 0
with open(Path('data') / 'title.principals.tsv', encoding='utf-8') as f:
    column = {}
    for i, p in enumerate(f.readline().strip().split('\t')):
        column[p.strip()] = i
    for li, line in enumerate(f):
        parts = line.strip().split('\t', len(column))
        category = parts[column['category']]
        job_max_len = max(job_max_len, len(parts[column['job']]))
        if category != '\\N':
            tp_categories[category] += 1
        if parts[column['characters']] != r'\N':
            chars.update(json.loads(parts[column['characters']]))
print(perf_counter() - t1, 's')

130.6693641100428 s


In [4]:
print('job_max_len:', job_max_len)
pprint(tp_categories)

job_max_len: 286
Counter({'actor': 13441424,
         'self': 10560091,
         'actress': 10489927,
         'writer': 8494665,
         'director': 7005873,
         'producer': 3943935,
         'cinematographer': 2067729,
         'composer': 2013765,
         'editor': 2012579,
         'archive_footage': 404370,
         'production_designer': 383677,
         'archive_sound': 4793})


In [10]:
print(len(chars), chars.total())
pprint(chars.most_common(100))

2735521 30382085
[('Self', 4546843),
 ('Self - Host', 1878474),
 ('Self - Presenter', 327377),
 ('Self - Guest', 325307),
 ('Self - Panelist', 250371),
 ('Self - Co-Host', 240752),
 ('Self - Contestant', 237169),
 ('Narrator', 170928),
 ('Themselves', 123295),
 ('Self - Judge', 116250),
 ('Self - Announcer', 111500),
 ('Self - Reporter', 95146),
 ('Self - Hostess', 94778),
 ('Self - Correspondent', 79159),
 ('Various', 74727),
 ('Self - Newsreader', 65513),
 ('Self - Narrator', 58859),
 ('Host', 53434),
 ('Self - Housemate', 46139),
 ('Self - Co-Hostess', 45536),
 ('Presenter', 44458),
 ('Self - Co-Anchor', 42368),
 ('Self - Anchor', 39588),
 ('Self - Model', 37613),
 ('Presented by', 36132),
 ('Additional Voices', 35325),
 ('Various Characters', 34330),
 ('Self - Interviewee', 32986),
 ('Self - Analyst', 29627),
 ('Self - Commentator', 28864),
 ('Self - Musical Guest', 22758),
 ('Self - Panellist', 22155),
 ('Self - Performer', 21038),
 ('Self - Celebrity Contestant', 18933),
 ('Self 

In [12]:
with open('enums.json', 'w', encoding='utf-8') as f:
    json.dump({'profession': list(sorted(profession.keys())),
               'title_type': list(sorted(title_types.keys())),
               'genre': list(sorted(genres.keys())), 
               't_aka_type': list(sorted(taka_types.keys())), 
               'region': list(sorted(taka_region.keys())), 
               'language': list(sorted(taka_lang.keys())),
               'category': list(sorted(tp_categories.keys())),
               'character': list(sorted(chars.keys()))
              },
             f,
             indent=2)